In [1]:
import os
import h5py
import random
from pathlib import Path
import numpy as np
import pandas as pd
import tensorflow as tf
import scipy.interpolate as spi
import scipy.signal as spsig
import scipy.stats as sps
from sleepkit.datasets import MesaDataset
from sleepkit.defines import SKTask, SKMode, SKTrainParams
import plotly.graph_objects as go
import plotly.express as px
import physiokit as pk

2023-09-19 11:41:40.545441: I tensorflow/core/util/port.cc:110] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2023-09-19 11:41:40.565935: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-09-19 11:41:40.882740: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [2]:
signals = ["Pleth", "SpO2", "Leg"]
features = ["HR", ""]

params = SKTrainParams(
    job_dir=Path("../results/mesa-lstm"),
    ds_path=Path("/home/vscode/datasets"),
    sampling_rate=64,
    frame_size=64*30,
    samples_per_subject=100,
)

In [3]:
ds = MesaDataset(
    ds_path=params.ds_path,
    frame_size=params.frame_size,
    target_rate=params.sampling_rate,
    is_commercial=True
)


In [4]:
subject_id = ds.train_subject_ids[412]
data_size = ds.get_subject_duration(subject_id=subject_id)*params.sampling_rate
print(data_size)

2764736


In [6]:
sleep_stages = ds.extract_sleep_stages(subject_id=subject_id)
sleep_mask = ds.sleep_stages_to_mask(sleep_stages=sleep_stages, data_size=data_size)
features = np.zeros((data_size // params.frame_size, 6), dtype=np.float32)
sleep_stages = np.zeros((data_size // params.frame_size), dtype=np.int32)
ts = np.arange(features.shape[0])

In [126]:
subject_id = ds.train_subject_ids[18]
data_size = ds.get_subject_duration(subject_id)*params.sampling_rate
ppg = ds.load_signal_for_subject(subject_id, "Pleth", start=0, data_size=data_size)
sleep_stages = ds.extract_sleep_stages(subject_id=subject_id)
sleep_mask = ds.sleep_stages_to_mask(sleep_stages=sleep_stages, data_size=data_size)

In [161]:
ppg = pk.ppg.clean(ppg, sample_rate=params.sampling_rate)
rpeaks = pk.ppg.find_peaks(ppg, sample_rate=params.sampling_rate)
rri = pk.ppg.compute_rr_intervals(rpeaks)
rri_mask = pk.ppg.filter_rr_intervals(rri, sample_rate=ds.target_rate, min_rr=0.1, max_rr=4, min_delta=0.5)
rri_itr = spi.interp1d(rpeaks[rri_mask == 0], rri[rri_mask == 0], kind="linear", fill_value="extrapolate")(np.arange(data_size))


In [162]:
min_idx, max_idx = (rpeaks[rri_mask == 0][0], rpeaks[rri_mask == 0][-1])

In [163]:
np.sum(rri_mask)

2338

In [164]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=np.arange(rri[rri_mask == 0].shape[0]), y=rri[rri_mask == 0], name="PPG"))
#fig.add_trace(go.Scatter(x=np.arange(data_size)[min_idx:max_idx:1000], y=rri_itr[min_idx:max_idx:1000], name="PPG"))

In [165]:
df = pd.DataFrame(dict(hrn=rri_itr[min_idx:max_idx:128][:-1], hrp=rri_itr[min_idx:max_idx:128][1:], sleep=sleep_mask[min_idx:max_idx:128][:-1]))

In [166]:
for i, start in enumerate(range(0, data_size - params.frame_size + 1, params.frame_size)):
    ppg = ds.load_signal_for_subject(subject_id, "Pleth", start=start, data_size=ds.frame_size)
    spo2 = ds.load_signal_for_subject(subject_id, "SpO2", start=start, data_size=ds.frame_size)
    leg = ds.load_signal_for_subject(subject_id, "Leg", start=start, data_size=ds.frame_size)
    spo2_status = ds.load_signal_for_subject(subject_id, "OxStatus", start=start, data_size=ds.frame_size)   
    ppg = pk.ppg.clean(ppg, sample_rate=params.sampling_rate)
    hr = pk.ppg.compute_heart_rate(ppg, sample_rate=params.sampling_rate, method="fft")

    spo2_mu = np.NAN
    spo2_std = np.NAN
    
    if np.sum(spo2_status > 1) < 0.80*spo2_status.size:
        spo2[spo2_status > 1] = np.median(spo2[spo2_status <= 1])
        spo2 = pk.signal.rescale_signal(spo2, 70, 100, 0, 1, clip=True)
        spo2_mu = np.nanmean(spo2)  
        spo2_std = np.clip(np.nanstd(spo2), 0, 1)

    leg = np.abs(leg - np.nanmean(leg))
    mov = pk.signal.rescale_signal(leg, 0, 0.2, 0, 1, clip=False)
    mov_mu = np.nanmean(mov)
    mov_std = np.clip(np.nanstd(mov), 0, 1)

    sleep_stages[i] = sps.mode(sleep_mask[start:start+params.frame_size]).mode    


    rri_mu = np.NAN
    rri_std = np.NAN
    rpeaks = pk.ppg.find_peaks(ppg, sample_rate=params.sampling_rate)
    if rpeaks.size >= 4:
        rri = pk.ppg.compute_rr_intervals(rpeaks)
        rri_mask = pk.ppg.filter_rr_intervals(rri, sample_rate=params.sampling_rate, min_rr=0.5, max_rr=2)
        if np.any(rri_mask == 1) and np.any(rri_mask == 0):
            rri[rri_mask == 1] = np.median(rri[rri_mask == 0])
        if np.any(rri_mask == 0):
            rri = pk.signal.rescale_signal(1000*rri/params.sampling_rate, 500, 2000, 0, 1, clip=True)
            rri_mu = np.nanmean(rri)
            rri_std = np.clip(np.nanstd(rri), 0, 1)
        # END IF
    # END IF

    features[i, 0] = rri_mu
    features[i, 1] = rri_std
    features[i, 2] = spo2_mu  
    features[i, 3] = spo2_std
    features[i, 4] = mov_mu 
    features[i, 5] = mov_std
# END FOR

IndexError: list assignment index out of range

In [ ]:
# RRI mean: [500, 1500] -> [0, 1]
# RRI std: clip(0, 1)

# SPO2 mean: [70, 100] -> [0, 1]
# SPO2 std: clip(0, 1)
# MOV mean: [0, 0.2] -> [0, 1]
# MOV std: clip(0, 1)

# rr_func = spi.PchipInterpolator(x=rpeaks[rr_mask == 0], y=rr_intervals[rr_mask == 0], extrapolate=True)
# inst_rr = rr_func(np.arange(params.frame_size))



In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=features[:, 0], name="RRI-MU"))
fig.add_trace(go.Scatter(x=ts, y=features[:, 1], name="RRI-SD"))
fig.add_trace(go.Scatter(x=ts, y=features[:, 2], name="SPO2-MU"))
fig.add_trace(go.Scatter(x=ts, y=features[:, 3], name="SPO2-STD"))
fig.add_trace(go.Scatter(x=ts, y=features[:, 4], name="MOV-MU"))
fig.add_trace(go.Scatter(x=ts, y=features[:, 5], name="MOV-STD"))

# fig.add_trace(go.Scatter(x=ts, y=100*sleep_stages.squeeze(), name="Sleep stages", line_shape="vh"))

sleep_boundaries = np.concatenate(([0], np.diff(sleep_stages).nonzero()[0]+1))
for i in range(1, len(sleep_boundaries)):
    start = sleep_boundaries[i-1]
    stop = sleep_boundaries[i]
    stage = sleep_stages[start]
    color_map = {1: "yellow", 2: "orange", 3: "red", 4: "purple", 5: "blue"}
    fig.add_vrect(x0=start, x1=stop, fillcolor=color_map.get(stage, None), opacity=0.4, layer="below", line_width=0)
fig.show()

In [ ]:
feature_names = [" RRI-MU", " RRI-SD", "SPO2-MU", "SPO2-SD", " MOV-MU", " MOV-SD"]
t_start = 200
t_end = 1000
for feat_idx, feature_name in enumerate(feature_names):
    print(f"{feature_name}", end="|\t")
    print((
        f"    W: {np.nanmedian(features[t_start:t_end][sleep_stages[t_start:t_end] == 0, feat_idx]):0.2f}  "
        f"   N1: {np.nanmedian(features[t_start:t_end][sleep_stages[t_start:t_end] == 1, feat_idx]):0.2f}  "
        f"   N2: {np.nanmedian(features[t_start:t_end][sleep_stages[t_start:t_end] == 2, feat_idx]):0.2f}  "
        f"N3/N4: {np.nanmedian(features[t_start:t_end][sleep_stages[t_start:t_end] == 3, feat_idx]):0.2f}  "
        f"  REM: {np.nanmedian(features[t_start:t_end][sleep_stages[t_start:t_end] == 5, feat_idx]):0.2f}  "
    ))

In [ ]:
target_subject_ids = ds.train_subject_ids
random.shuffle(target_subject_ids)
target_subject_ids = target_subject_ids[:1000]
num_samples = 10
results = np.zeros((len(target_subject_ids), num_samples, 2), dtype=np.float32)
for pt, subject_id in enumerate(target_subject_ids):
    print(f"Processing subject {subject_id} {pt}")
    dj = 0
    pt_duration = ds.get_subject_duration(subject_id=subject_id)*ds.target_rate
    attempts = 0
    while (dj < num_samples) and (attempts < 100):
        start = random.randint(ds.frame_size, int(pt_duration - 2*ds.frame_size))
        ppg = ds.load_signal_for_subject(subject_id, "Pleth", start=start, data_size=ds.frame_size)
        rsp = ds.load_signal_for_subject(subject_id, "Therm", start=start, data_size=ds.frame_size)
        leg = ds.load_signal_for_subject(subject_id, "Leg", start=start, data_size=ds.frame_size)
        sig_quality = ds.load_signal_for_subject(subject_id, "OxStatus", start=start, data_size=ds.frame_size)
        sig_quality = np.round(sig_quality)
        if sig_quality[sig_quality > 1].size > 0.2*sig_quality.size:
            attempts += 1
            continue

        hr = pk.ppg.compute_heart_rate(ppg, sample_rate=params.sampling_rate, method="fft")
        min_rr = max(0.5, 60/hr - 0.25)
        max_rr = min(4, 60/hr + 0.25)
        ppg = pk.signal.filter_signal(ppg, lowcut=1/max_rr, highcut=1/min_rr, sample_rate=params.sampling_rate)
        rsp = pk.signal.filter_signal(rsp, lowcut=0.05, highcut=1, order=3, sample_rate=params.sampling_rate)
        leg = pk.signal.filter_signal(leg, lowcut=0.05, highcut=1, order=3, sample_rate=params.sampling_rate)

        rpeaks = pk.ppg.find_peaks(ppg, sample_rate=params.sampling_rate)
        if rpeaks.size < 4:
            attempts += 1
            continue

        rri = pk.ppg.compute_rr_intervals(rpeaks)
        rri_mask = pk.ppg.filter_rr_intervals(rri, sample_rate=params.sampling_rate, min_rr=min_rr, max_rr=max_rr)

        # rpeaks = rpeaks[rri_mask == 0]
        # rri = rri[rri_mask == 0]

        if rpeaks.size < 4: 
            attempts += 1
            continue

        rtroughs = np.zeros_like(rpeaks)
        for i in range(0, len(rpeaks)-1):
            rtroughs[i] = np.argmin(ppg[rpeaks[i]:rpeaks[i+1]]) + rpeaks[i]

        rtroughs[-1] = rtroughs[-2]
        # rpeaks = rpeaks[:-1]
        # rri = rri[:-1]

        riav = ppg[rpeaks] - ppg[rtroughs]
        riiv = ppg[rpeaks]
        rifv = rri

        riav = spi.interp1d(rpeaks, riav, kind="linear", fill_value="extrapolate")(np.arange(ds.frame_size))
        riiv = spi.interp1d(rpeaks, riiv, kind="linear", fill_value="extrapolate")(np.arange(ds.frame_size))
        rifv = spi.interp1d(rpeaks[rri_mask == 0], rifv[rri_mask == 0], kind="cubic", fill_value="extrapolate")(np.arange(ds.frame_size))

        riav = pk.signal.filter_signal(riav, lowcut=0.1, highcut=0.5, sample_rate=params.sampling_rate)
        riiv = pk.signal.filter_signal(riiv, lowcut=0.1, highcut=0.5, sample_rate=params.sampling_rate)
        rifv = pk.signal.filter_signal(rifv, lowcut=0.1, highcut=0.5, sample_rate=params.sampling_rate)

        freqs, ppg_sp = pk.ppg.compute_fft(ppg, sample_rate=params.sampling_rate)
        freqs, rsp_sp = pk.ppg.compute_fft(rsp, sample_rate=params.sampling_rate)
        freqs, leg_sp = pk.ppg.compute_fft(leg, sample_rate=params.sampling_rate)

        freqs, riav_sp = pk.ppg.compute_fft(riav, sample_rate=params.sampling_rate)
        freqs, riiv_sp = pk.ppg.compute_fft(riiv, sample_rate=params.sampling_rate)
        freqs, rifv_sp = pk.ppg.compute_fft(rifv, sample_rate=params.sampling_rate)

        f_left = np.where(freqs >= 0.10)[0][0]
        f_right = np.where(freqs >= 1.00)[0][0]
        freqs = freqs[f_left:f_right]
        ppg_sp = np.abs(ppg_sp[f_left:f_right])
        rsp_sp = np.abs(rsp_sp[f_left:f_right])
        leg_sp = np.abs(leg_sp[f_left:f_right])
        riav_sp = np.abs(riav_sp[f_left:f_right])
        riiv_sp = np.abs(riiv_sp[f_left:f_right])
        rifv_sp = np.abs(rifv_sp[f_left:f_right])
        ppg_sp = ppg_sp/np.sum(ppg_sp)
        leg_sp = leg_sp/np.sum(leg_sp)
        rsp_sp = rsp_sp/np.sum(rsp_sp)
        riav_sp = riav_sp/np.sum(riav_sp)
        riiv_sp = riiv_sp/np.sum(riiv_sp)
        rifv_sp = rifv_sp/np.sum(rifv_sp)
        rrsp_sp = (3*riav_sp + 3*riiv_sp + 3*rifv_sp + 1*leg_sp + 0*ppg_sp)/10

        true_freq_idx = np.argmax(rsp_sp)
        pred_freq_idx = np.argmax(rrsp_sp)
        if rsp_sp[true_freq_idx] < 0.20 or rrsp_sp[pred_freq_idx] < 0.20:
            attempts += 1
            continue

        results[pt, dj, 0] = freqs[true_freq_idx]
        results[pt, dj, 1] = freqs[pred_freq_idx]
        dj += 1
        attempts = 0


In [ ]:
y_true = 60*results[:,:,0].flatten()
y_pred = 60*results[:,:,1].flatten()
valid_idx = y_true > 0
y_true = y_true[valid_idx]
y_pred = y_pred[valid_idx]
fig = go.Figure()
fig.add_trace(go.Violin(y=100*(y_true-y_pred)/y_true, box_visible=True, meanline_visible=True, name="Error"))
# fig.add_trace(go.Scatter(x=y_true, y=y_pred, opacity=0.3, mode="markers"))
fig.show()

In [5]:
subject_idx = 3
offset = params.sampling_rate*60*150
subject_id = ds.train_subject_ids[subject_idx]

sleep_stages = ds.extract_sleep_stages(subject_id=subject_id)
sleep_stages = ds.sleep_stages_to_mask(sleep_stages=sleep_stages, data_size=int(offset+params.frame_size))
sleep_stages = sleep_stages[offset:]

raw_ppg = ds.load_signal_for_subject(subject_id, "Pleth", start=offset, data_size=ds.frame_size)
rsp = ds.load_signal_for_subject(subject_id, "Therm", start=offset, data_size=ds.frame_size)
leg = ds.load_signal_for_subject(subject_id, "Leg", start=offset, data_size=ds.frame_size)
ox_status = ds.load_signal_for_subject(subject_id, "OxStatus", start=offset, data_size=ds.frame_size)

hr = pk.ppg.compute_heart_rate(raw_ppg, sample_rate=params.sampling_rate, method="fft")
min_rr = max(0.5, 60/hr - 0.5)
max_rr = min(4, 60/hr + 0.5)
print(min_rr, max_rr, hr)
ppg = pk.signal.filter_signal(raw_ppg, lowcut=0.5, highcut=4.0, order=5, sample_rate=params.sampling_rate)
rsp = pk.signal.filter_signal(rsp, lowcut=0.10, highcut=0.5, order=3, sample_rate=params.sampling_rate)
mov = pk.signal.filter_signal(leg, lowcut=3.0, highcut=11, order=3, sample_rate=params.sampling_rate)
leg = pk.signal.filter_signal(leg, lowcut=0.05, highcut=1, order=3, sample_rate=params.sampling_rate)

rpeaks = pk.ppg.find_peaks(ppg, sample_rate=params.sampling_rate)
# Handle no peaks
rri = pk.ppg.compute_rr_intervals(rpeaks)
rri_mask = pk.ppg.filter_rr_intervals(rri, sample_rate=params.sampling_rate, min_rr=min_rr, max_rr=max_rr)

rtroughs = np.zeros_like(rpeaks)
for i in range(0, len(rpeaks)-1):
    rtroughs[i] = np.argmin(ppg[rpeaks[i]:rpeaks[i+1]]) + rpeaks[i]
# END FOR

rtroughs = rtroughs[1:-1]
rpeaks = rpeaks[1:-1]
rri = rri[1:-1]
rri_mask = rri_mask[1:-1]

bpeaks = pk.rsp.find_peaks(rsp, sample_rate=params.sampling_rate)
btroughs = np.zeros_like(bpeaks)
for i in range(0, len(bpeaks)-1):
    btroughs[i] = np.argmin(rsp[bpeaks[i]:bpeaks[i+1]]) + bpeaks[i]
# END FOR

riav = ppg[rpeaks] - ppg[rtroughs]
riav_mu, riav_std = np.median(riav), sps.iqr(riav)
riav = np.clip(riav, riav_mu - riav_std, riav_mu + riav_std) 

riiv = ppg[rpeaks]
rifv = rri
# rifv[rri_mask == 1] = np.median(rifv[rri_mask == 0])

riav = spi.interp1d(rpeaks, riav, kind="linear", fill_value="extrapolate")(np.arange(ppg.size))
riiv = spi.interp1d(rpeaks[rri_mask == 0], riiv[rri_mask == 0], kind="linear", fill_value="extrapolate")(np.arange(ppg.size))
rifv = spi.interp1d(rpeaks, rifv, kind="linear", fill_value="extrapolate")(np.arange(ppg.size))

riav = pk.signal.filter_signal(riav, lowcut=0.16, highcut=1.0, sample_rate=params.sampling_rate)
riiv = pk.signal.filter_signal(riiv, lowcut=0.16, highcut=1.0, sample_rate=params.sampling_rate)
rifv = pk.signal.filter_signal(rifv, lowcut=0.16, highcut=1.0, sample_rate=params.sampling_rate)

# riav[ox_status > 1] = 0
# riiv[ox_status > 1] = 0
# rifv[ox_status > 1] = 0


0.5 1.1666666666666665 90.0


In [14]:
bpeaks

array([  76,  405,  696,  935, 1170, 1387, 1565, 1825])

In [20]:
fig = go.Figure()
ts = np.arange(ppg.size)
fig.add_trace(go.Scatter(x=ts, y=raw_ppg, name="Raw PPG"))
fig.add_trace(go.Scatter(x=ts, y=ppg, name="PPG"))
fig.add_trace(go.Scatter(x=ts, y=rsp, name="RSP")) 
fig.add_trace(go.Scatter(x=bpeaks, y=rsp[bpeaks], mode="markers", name="B-PEAKS")) 
fig.add_trace(go.Scatter(x=btroughs, y=rsp[btroughs], mode="markers", name="B-TROUGHS")) 
fig.add_trace(go.Scatter(x=ts, y=ox_status, name="OX", line_shape="vh"))
# fig.add_trace(go.Scatter(x=np.arange(leg.size), y=leg, name="LEG"))
#fig.add_trace(go.Scatter(x=rpeaks[rri_mask == 0], y=ppg[rpeaks[rri_mask == 0]], mode="markers", name="R-PEAKS"))
#fig.add_trace(go.Scatter(x=rpeaks[rri_mask == 1], y=ppg[rpeaks[rri_mask == 1]], mode="markers", name="R-PEAKS (MASKED)"))
#fig.add_trace(go.Scatter(x=rtroughs, y=ppg[rtroughs], mode="markers", name="R-TR"))

fig.show()

In [7]:
fig = go.Figure()
# fig.add_trace(go.Scatter(x=np.arange(ppg.size), y=ppg_raw, name="PPG-R"))
# fig.add_trace(go.Scatter(x=np.arange(ppg.size), y=ppg, name="PPG"))
# fig.add_trace(go.Scatter(x=np.arange(ppg.size), y=rsp, name="RSP")) 
# # fig.add_trace(go.Scatter(x=np.arange(leg.size), y=leg, name="LEG"))
# fig.add_trace(go.Scatter(x=rpeaks, y=ppg[rpeaks], mode="markers", name="R-PEAKS"))
# fig.add_trace(go.Scatter(x=rtroughs, y=ppg[rtroughs], mode="markers", name="R-TR"))

# fig.add_trace(go.Scatter(x=np.arange(ppg.size), y=riav, name="RIAV"))
# fig.add_trace(go.Scatter(x=np.arange(ppg.size), y=riiv, name="RIIV"))
fig.add_trace(go.Scatter(x=np.arange(rifv.size), y=rifv, name="RIFV", mode="markers"))

# fig.add_trace(go.Scatter(x=np.arange(ppg.size), y=100*sleep_stages, name="Sleep stages", line_shape="vh"))

fig.show()

In [22]:
freqs, ppg_sp = pk.ppg.compute_fft(ppg, sample_rate=params.sampling_rate)

freqs, rsp_sp = pk.ppg.compute_fft(rsp, sample_rate=params.sampling_rate)
freqs, leg_sp = pk.ppg.compute_fft(leg, sample_rate=params.sampling_rate)

freqs, riav_sp = pk.ppg.compute_fft(riav, sample_rate=params.sampling_rate)
freqs, riiv_sp = pk.ppg.compute_fft(riiv, sample_rate=params.sampling_rate)
freqs, rifv_sp = pk.ppg.compute_fft(rifv, sample_rate=params.sampling_rate)

f_left = np.where(freqs >= 0.0)[0][0]
f_right = np.where(freqs >= 1.00)[0][0]
freqs = freqs[f_left:f_right]
ppg_sp = np.abs(ppg_sp[f_left:f_right])
rsp_sp = np.abs(rsp_sp[f_left:f_right])
leg_sp = np.abs(leg_sp[f_left:f_right])
riav_sp = np.abs(riav_sp[f_left:f_right])
riiv_sp = np.abs(riiv_sp[f_left:f_right])
rifv_sp = np.abs(rifv_sp[f_left:f_right])
ppg_sp = ppg_sp/np.sum(ppg_sp)
leg_sp = leg_sp/np.sum(leg_sp)
rsp_sp = rsp_sp/np.sum(rsp_sp)
riav_sp = riav_sp/np.sum(riav_sp)
riiv_sp = riiv_sp/np.sum(riiv_sp)
rifv_sp = rifv_sp/np.sum(rifv_sp)
rrsp_sp = (3*riav_sp + 2*riiv_sp + 4*rifv_sp + 0*leg_sp + 0*ppg_sp)/10
rrsp_sp = (0*riav_sp + 0*riiv_sp + 10*rifv_sp + 0*leg_sp + 0*ppg_sp)/10
rsp_max_idx = np.argmax(rsp_sp)
rsp_freq_indices = np.where(rsp_sp >= 0.8*np.max(rsp_sp))[0]
rsp_bpm_weights = rsp_sp[rsp_freq_indices]
rsp_bpm = np.sum(rsp_bpm_weights*freqs[rsp_freq_indices])/np.sum(rsp_bpm_weights)

rrsp_max_idx = np.argmax(rrsp_sp)
rrsp_freq_indices = np.where(rrsp_sp >= 0.8*np.max(rrsp_sp))[0]
rrsp_bpm_weights = rrsp_sp[rrsp_freq_indices]
rrsp_bpm = np.sum(rrsp_bpm_weights*freqs[rrsp_freq_indices])/np.sum(rrsp_bpm_weights)
rrsp_qi = rrsp_sp[rrsp_max_idx]/np.mean(rrsp_sp)
print(freqs[rrsp_freq_indices])
print(f"ACT: {60*rsp_bpm:0.2f} BPM | PRED: {60*rrsp_bpm:0.2f} BPM QI: {rrsp_qi:0.2f}")

[0.46875 0.5    ]
ACT: 15.96 BPM | PRED: 29.04 BPM QI: 3.05


In [23]:
rsp_riav_bpm, riav_qi = pk.rsp.compute_respiratory_rate_from_ppg(ppg, peaks=rpeaks, troughs=rtroughs, sample_rate=params.sampling_rate, method="riav")
rsp_riiv_bpm, riiv_qi = pk.rsp.compute_respiratory_rate_from_ppg(ppg, peaks=rpeaks, sample_rate=params.sampling_rate, method="riiv")
rsp_rifv_bpm, rifv_qi = pk.rsp.compute_respiratory_rate_from_ppg(ppg, peaks=rpeaks, rri=rri, sample_rate=params.sampling_rate, method="rifv")
print(f"RIAV: {rsp_riav_bpm:0.2f} BPM | QI: {riav_qi:0.2f}")
print(f"RIIV: {rsp_riiv_bpm:0.2f} BPM | QI: {riiv_qi:0.2f}")
print(f"RIFV: {rsp_rifv_bpm:0.2f} BPM | QI: {rifv_qi:0.2f}")

RIAV: 29.03 BPM | QI: 5.95
RIIV: 29.04 BPM | QI: 6.27
RIFV: 19.53 BPM | QI: 9.50


In [16]:
ts = np.arange(rpeaks[0], rpeaks[-1], 1)

In [24]:
freqs2, rifv2_sp = spsig.welch(rifv, fs=params.sampling_rate, window="hann", nperseg=20*params.sampling_rate, noverlap=15*params.sampling_rate, average="median")
f_left = np.where(freqs2 >= 0.16)[0][0]
f_right = np.where(freqs2 >= 1.00)[0][0]
freqs2 = freqs2[f_left:f_right]

rifv2_sp = rifv2_sp[f_left:f_right]
rifv2_sp = rifv2_sp/np.sum(rifv2_sp)

rrsp_max_idx = np.argmax(rifv2_sp)
rrsp_freq_indices = np.where(rifv2_sp >= 0.8*np.max(rifv2_sp))[0]
rrsp_bpm_weights = rifv2_sp[rrsp_freq_indices]
rrsp_bpm = np.sum(rrsp_bpm_weights*freqs2[rrsp_freq_indices])/np.sum(rrsp_bpm_weights)

print(f"ACT: {60*rsp_bpm:0.2f} BPM | PRED: {60*rrsp_bpm:0.2f} BPM QI: {rrsp_qi:0.2f}")

ACT: 15.96 BPM | PRED: 23.03 BPM QI: 3.05


In [25]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=freqs, y=ppg_sp, name="PPG"))
fig.add_trace(go.Scatter(x=freqs, y=rsp_sp, name="RSP"))
fig.add_trace(go.Scatter(x=freqs, y=leg_sp, name="LEG"))
fig.add_trace(go.Scatter(x=freqs, y=riav_sp, name="RIAV"))
fig.add_trace(go.Scatter(x=freqs, y=riiv_sp, name="RIIV"))
fig.add_trace(go.Scatter(x=freqs, y=rifv_sp, name="RIFV"))
fig.add_trace(go.Scatter(x=freqs, y=rrsp_sp, name="RRSP"))
fig.show()

In [24]:
def compute_features_001(ds, subject_id, start):
    # Load signals
    ppg = ds.load_signal_for_subject(subject_id, "Pleth", start=start, data_size=ds.frame_size)
    spo2 = ds.load_signal_for_subject(subject_id, "SpO2", start=start, data_size=ds.frame_size)
    rsp = ds.load_signal_for_subject(subject_id, "Abdo", start=start, data_size=ds.frame_size)
    leg = ds.load_signal_for_subject(subject_id, "Leg", start=start, data_size=ds.frame_size)
    qos = ds.load_signal_for_subject(subject_id, "OxStatus", start=start, data_size=ds.frame_size)
    
    # Handle if signal is marked as bad
    if np.sum(qos > 1) > 0.60*qos.size:
        raise ValueError("Bad signal")
    
    #### Preprocess signals
    ppg = pk.ppg.clean(ppg, sample_rate=ds.target_rate)
    rsp = pk.rsp.clean(rsp, sample_rate=ds.target_rate)
    mov = pk.signal.filter_signal(leg, lowcut=3, highcut=11, order=3, sample_rate=ds.target_rate)
    
    hr_bpm = pk.ppg.compute_heart_rate(ppg, sample_rate=ds.target_rate, method="fft")
    rsp_bpm = pk.rsp.compute_respiratory_rate_from_fft(rsp, sample_rate=ds.target_rate, lowcut=0.05, highcut=1.0)

    min_rr, max_rr = max(0.5, 60/hr_bpm - 0.25), min(4, 60/hr_bpm + 0.25)
    min_rsp_rr, max_rsp_rr = 5/60, 60/60

    # HRV metrics
    rpeaks = pk.ppg.find_peaks(ppg, sample_rate=ds.target_rate)
    if rpeaks.size < 4:
        raise ValueError("Not enough peaks")

    rri = pk.ppg.compute_rr_intervals(rpeaks)
    rri_mask = pk.ppg.filter_rr_intervals(rri, sample_rate=ds.target_rate, min_rr=min_rr, max_rr=max_rr)
    hrv_td_metrics = pk.hrv.compute_hrv_time(rri[rri_mask == 0], sample_rate=ds.target_rate)
    hrv_fd_metrics = pk.hrv.compute_hrv_frequency(rpeaks, rri=rri, bands=[(0.04, 0.15), (0.15, 0.4)], sample_rate=ds.target_rate)

    #### Compute features
    spo2_mu = np.nanmean(spo2)
    spo2_std = np.nanstd(spo2)
    spo2_med = np.nanmedian(spo2)
    spo2_iqr = sps.iqr(spo2)

    mov_mu = np.nanmean(mov)
    mov_std = np.nanstd(mov)
    mov_med = np.nanmedian(mov)
    mov_iqr = sps.iqr(mov)

    rri_mu = hrv_td_metrics.mean_nn
    rri_std = hrv_td_metrics.sd_nn
    rri_med = hrv_td_metrics.meadian_nn
    rri_iqr = hrv_td_metrics.iqr_nn
    rri_sd_rms = hrv_td_metrics.rms_sd
    rri_sd_std = hrv_td_metrics.sd_sd

    hrv_lf = hrv_fd_metrics.bands[0].total_power
    hrv_hf = hrv_fd_metrics.bands[1].total_power
    hrv_lfhf = hrv_lf/hrv_hf

    # # Compute resipiratory rate from PPG / ACCEL
    # rtroughs = np.zeros_like(rpeaks)
    # for i in range(0, len(rpeaks)-1):
    #     rtroughs[i] = np.argmin(ppg[rpeaks[i]:rpeaks[i+1]]) + rpeaks[i]
    # # END FOR
    # rtroughs[-1] = rtroughs[-2]

    # rpeaks = rpeaks[rri_mask == 0]
    # rtroughs = rtroughs[rri_mask == 0]
    # rri = rri[rri_mask == 0]
    features = [
        spo2_mu, spo2_std, spo2_med, spo2_iqr, 
        mov_mu, mov_std, mov_med, mov_iqr, 
        rri_mu, rri_std, rri_med, rri_iqr, rri_sd_rms, rri_sd_std,
        hr_bpm, rsp_bpm,
        hrv_lf, hrv_hf, hrv_lfhf
    ]
    return features


def compute_dataset_001():
    feat_names = [
        "SPO2-mu", "SPO2-std", "SPO2-med", "SPO2-iqr",
        "MOV-mu", "MOV-std", "MOV-med", "MOV-iqr",
        "RRI-mu", "RRI-std", "RRI-med", "RRI-iqr", "RRI-sd-rms", "RRI-sd-std",
        "HR-bpm", "RSP-bpm", "HRV-lf", "HRV-hf", "HRV-lfhf"
    ]
    ds = MesaDataset(
        params.ds_path,
        frame_size=params.frame_size,
        target_rate=params.sampling_rate,
        is_commercial=True
    )    
    for subject_id in (ds.train_subject_ids+ds.test_subject_ids):
        print(".", end="")
        subject_duration = ds.get_subject_duration(subject_id=subject_id)*ds.target_rate
        sleep_stages = ds.extract_sleep_stages(subject_id=subject_id)
        sleep_mask = ds.sleep_stages_to_mask(sleep_stages=sleep_stages, data_size=subject_duration)
        features = np.zeros((subject_duration // params.frame_size, len(feat_names)), dtype=np.float32)
        sleep_stages = np.zeros((subject_duration // params.frame_size), dtype=np.int32) 
        mask = np.zeros((subject_duration // params.frame_size), dtype=np.int32)    
        for f_idx, start in enumerate(range(0, subject_duration - params.frame_size, params.frame_size)): 
            try:
                features[f_idx] = compute_features_001(ds, subject_id, start)
                sleep_stages[f_idx] = sps.mode(sleep_mask[start:start+params.frame_size]).mode  
                mask[f_idx] = 1
            except ValueError:
                continue
        # END FOR
        subj_path = Path(f"..", "datasets", "processed", "mesa-fs001")
        os.makedirs(subj_path, exist_ok=True)
        with h5py.File(str(subj_path / f"{subject_id}.h5"), "w") as h5:
            h5.create_dataset(f"/features", data=features, compression="gzip", compression_opts=6)
            h5.create_dataset(f"/labels", data=sleep_stages, compression="gzip", compression_opts=6)     
            h5.create_dataset(f"/mask", data=mask, compression="gzip", compression_opts=6)
        # END WITH
    # END FOR
    h5.close()


In [25]:
features, sleep_stages, mask = compute_dataset_001()

........................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................

TypeError: cannot unpack non-iterable NoneType object

In [21]:
Path(f"..", "datasets" "processed", "mesa-fs001")

In [15]:
features.shape

(1319, 19)

In [62]:
set(sleep_stages)

{0, 1, 2, 3, 5}

In [22]:
ts = np.arange(features.shape[0])
fig = go.Figure()
for f in range(features.shape[1]):
    y = np.where(mask == 0, features[:,f], np.nan)
    y = (y - np.nanmean(y))/np.nanstd(y)
    fig.add_trace(go.Scatter(x=ts, y=y, name=feat_names[f]))
sleep_boundaries = np.concatenate(([0], np.diff(sleep_stages).nonzero()[0]+1))
for i in range(1, len(sleep_boundaries)):
    start = sleep_boundaries[i-1]
    stop = sleep_boundaries[i]
    stage = sleep_stages[start]
    color_map = {0: "white", 1: "yellow", 2: "orange", 3: "red", 4: "purple", 5: "blue"}
    fig.add_vrect(x0=start, x1=stop, fillcolor=color_map.get(stage, None), opacity=0.4, layer="below", line_width=0)
fig.show()

In [24]:
df = pd.DataFrame(features, columns=feat_names)

In [26]:
df["sleep_stage"] = sleep_stages

In [167]:
fig = px.scatter(df.head(200000), x="hrn", y="hrp", color="sleep", opacity=0.3)
fig.show()

In [151]:
df.shape

(249927, 3)

In [ ]:
# For each patient, window, compute features and sleep stage -> save to parquet
#  